# Constructs ```coordinates_mask``` file
The ```coordinates_mask``` file is needed to run MOSAIX, to build interpolation weights for the coupled model

Olivier Marti - olivier.marti@lsce.ipsl - 10/06/2021

In [1]:
import xarray as xr
import numpy  as np
import nemo
import datetime, os, platform

# Input files, type of ORCA grid, and output file

In [2]:
#model   = 'eORCA1.2'
model   = 'ORCA2.3'
#model   = 'ORCA2.4'

In [5]:
if model == 'eORCA1.2' :
    n_coord = 'eORCA_R1_coordinates_v1.0.nc' 
    n_bathy = 'eORCA_R1_bathy_meter_v2.2.nc'
    #n_coord = 'https://vesg.ipsl.upmc.fr/thredds/dodsC/work/p86mart/GRAF/DATA/eORCA_R1_coordinates_v1.0.nc'
    #n_bathy = 'https://vesg.ipsl.upmc.fr/thredds/dodsC/work/p86mart/GRAF/DATA/eORCA_R1_bathy_meter_v2.2.nc'
    nperio  = 6
    n_out   = 'eORCA_R1_coordinates_mask_test.nc'

if model == 'ORCA2.3' :
    nperio  = 4
    n_coord = 'coordinates_ORCA2_LIM3_PISCES.nc' #'ORCA2.3_coordinates.nc' #'coordinates.nc' # 
    n_bathy = 'bathy_meter_ORCA2_LIM3_PISCES.nc' #'ORCA2.3_bathy_meter.nc' #'bathy_meter_closea_topo.nc' # 
    n_out   = 'My_test.nc'
    
if model == 'ORCA2.4' :
    nperio  = 4
    n_coord = 'ORCA2.4_coordinates.nc'
    n_bathy = 'ORCA2.4_bathy_meter.nc'
    n_out   = 'ORCA2.4_coordinates_mask_test.nc'

## Open input files
Do not decode time which might be buggy in soem files
Suppress singleton dimensions if necessary

In [6]:
f_coord = xr.open_dataset (n_coord, decode_times=False).squeeze()
f_bathy = xr.open_dataset (n_bathy, decode_times=False).squeeze()

In [7]:
# Suppress time if necessary
try    :
    del f_coord['time']
    print ('success')
except :
    pass
    print ('failed to suppress time')

success


## Creates masks

### Read bathymetry 

In [8]:
Bathymetry = f_bathy['Bathymetry']

try :
    Bathymetry = Bathymetry.rename ({'nav_lat':'nav_lat_grid_T', 'nav_lon':'nav_lon_grid_T'})
    print ('Normal case')
except : 
    print ('Exception')
    nav_lon_grid_T = f_bathy ['nav_lon']
    nav_lat_grid_T = f_bathy ['nav_lat']
    Bathymetry = xr.DataArray (Bathymetry, coords = { "nav_lat_grid_T": (["y", "x"], nav_lat_grid_T),
                                                      "nav_lon_grid_T": (["y", "x"], nav_lon_grid_T) } )
    
Bathymetry = Bathymetry.rename ({'y':'y_grid_T', 'x':'x_grid_T'})

Exception


In [9]:
if model == 'ORCA2.3' :
    # orca_r2: Gibraltar strait open
    Bathymetry[101,139] = 284.
    # orca_r2: Bab el Mandeb strait open
    Bathymetry[87,159] = 137.

### Determine which periodicity is needed

In [10]:
jpj, jpi = Bathymetry.shape
try : 
    if nperio != None :
        print ('nperio specified : ', nperio)
except :
    nperio = None
    if jpi ==  182 : nperio = 4 # ORCA2. \!/ We choose legacy orca2
    if jpi ==  362 : nperio = 6 # ORCA1.
    if jpi == 1442 : nperio = 6 # ORCA025.
    #
    if nperio == None :
        sys.exit ('nperio not found, and cannot by guessed' )
    else :
        print ('nperio set as {:d} (deduced from data size {:d} {:d})'.format (nperio, jpj, jpi))

nperio specified :  4


In [11]:
Bathymetry = nemo.lbc (Bathymetry, nperio=nperio, cd_type='T')

### Creates ```mask_T```

In [12]:
mask_T = xr.where (Bathymetry - 1. + 0.1 >= 0.0, 1, 0).astype (dtype='int8')

### Creates other masks

In [14]:
mask_U = mask_T * mask_T.shift (x_grid_T=-1)
mask_V = mask_T * mask_T.shift (y_grid_T=-1)
mask_F = mask_T * mask_T.shift (y_grid_T=-1) * mask_T.shift (x_grid_T=-1) * mask_T.shift (y_grid_T=-1, x_grid_T=-1)
mask_W = mask_T

mask_U = nemo.lbc (mask_U, nperio=nperio, cd_type='U', nemo_4U_bug=True).astype (dtype='int8')
mask_V = nemo.lbc (mask_V, nperio=nperio, cd_type='V').astype (dtype='int8')
mask_F = nemo.lbc (mask_F, nperio=nperio, cd_type='F').astype (dtype='int8')
mask_W = nemo.lbc (mask_W, nperio=nperio, cd_type='W').astype (dtype='int8')

mask_U = mask_U.rename ( {'y_grid_T'      : 'y_grid_U'      , 'x_grid_T'      : 'x_grid_U', 
                          'nav_lat_grid_T': 'nav_lat_grid_U', 'nav_lon_grid_T': 'nav_lon_grid_U'} )
mask_V = mask_V.rename ( {'y_grid_T'      : 'y_grid_V'      , 'x_grid_T'      : 'x_grid_V',
                          'nav_lat_grid_T': 'nav_lat_grid_V', 'nav_lon_grid_T': 'nav_lon_grid_V'} )
mask_W = mask_W.rename ( {'y_grid_T'      : 'y_grid_W'      , 'x_grid_T'      : 'x_grid_W',
                          'nav_lat_grid_T': 'nav_lat_grid_W', 'nav_lon_grid_T': 'nav_lon_grid_W'} )
mask_F = mask_F.rename ( {'y_grid_T'      : 'y_grid_F'      , 'x_grid_T'      : 'x_grid_F',
                          'nav_lat_grid_T': 'nav_lat_grid_F', 'nav_lon_grid_T': 'nav_lon_grid_F'} )

mask_T.name = 'mask_T'
mask_U.name = 'mask_U'
mask_V.name = 'mask_V'
mask_F.name = 'mask_F'
mask_W.name = 'mask_W'

### Masks with duplicate points removed

In [ ]:
#maskutil_T = nemo.lbc_mask (mask_T, nperio=nperio, cd_type='T')
#maskutil_U = nemo.lbc_mask (mask_U, nperio=nperio, cd_type='U')
#maskutil_V = nemo.lbc_mask (mask_V, nperio=nperio, cd_type='V')
#maskutil_F = nemo.lbc_mask (mask_F, nperio=nperio, cd_type='F')
#maskutil_W = nemo.lbc_mask (mask_W, nperio=nperio, cd_type='W')

#maskutil_T.name = 'maskutil_T'
#maskutil_U.name = 'maskutil_U'
#maskutil_V.name = 'maskutil_V'
#maskutil_F.name = 'maskutil_F'
#maskutil_W.name = 'maskutil_W'

In [15]:
# Plus compact que ci-dessus, mais un peu incompréhensible .... !!!
for cd_type in ['T', 'U', 'V', 'F', 'W'] :
    MaskName = 'mask_'     + cd_type
    UtilName = 'maskutil_' + cd_type
    locals()[UtilName] = nemo.lbc_mask (locals()[MaskName], nperio=nperio, cd_type=cd_type)
    locals()[UtilName].name = UtilName

### Add attributes

In [16]:
mask_T.attrs    ['cell_measures'] = 'area: area_grid_T'
mask_U.attrs    ['cell_measures'] = 'area: area_grid_U'
mask_V.attrs    ['cell_measures'] = 'area: area_grid_V'
mask_W.attrs    ['cell_measures'] = 'area: area_grid_W'
mask_F.attrs    ['cell_measures'] = 'area: area_grid_F'

maskutil_T.attrs['cell_measures'] = 'area: area_grid_T'
maskutil_U.attrs['cell_measures'] = 'area: area_grid_U'
maskutil_V.attrs['cell_measures'] = 'area: area_grid_V'
maskutil_W.attrs['cell_measures'] = 'area: area_grid_W'
maskutil_F.attrs['cell_measures'] = 'area: area_grid_F'

## Creates grid coordinates and surfaces

In [17]:
nav_lon_grid_T = nemo.lbc (f_coord ['glamt'], nperio=nperio, cd_type='T')
nav_lat_grid_T = nemo.lbc (f_coord ['gphit'], nperio=nperio, cd_type='T')
nav_lon_grid_U = nemo.lbc (f_coord ['glamu'], nperio=nperio, cd_type='U',nemo_4U_bug=True)
#nav_lon_grid_U = f_coord ['glamu']
nav_lat_grid_U = nemo.lbc (f_coord ['gphiu'], nperio=nperio, cd_type='U',nemo_4U_bug=True)
#nav_lat_grid_U = f_coord ['gphiu']
nav_lon_grid_V = nemo.lbc (f_coord ['glamv'], nperio=nperio, cd_type='V')
nav_lat_grid_V = nemo.lbc (f_coord ['gphiv'], nperio=nperio, cd_type='V')
nav_lon_grid_W = nemo.lbc (f_coord ['glamt'], nperio=nperio, cd_type='W')
nav_lat_grid_W = nemo.lbc (f_coord ['gphit'], nperio=nperio, cd_type='W')
nav_lon_grid_F = nemo.lbc (f_coord ['glamf'], nperio=nperio, cd_type='F')
nav_lat_grid_F = nemo.lbc (f_coord ['gphif'], nperio=nperio, cd_type='F')

nav_lon_grid_T = nav_lon_grid_T.rename( {'y':'y_grid_T', 'x':'x_grid_T'} )
nav_lat_grid_T = nav_lat_grid_T.rename( {'y':'y_grid_T', 'x':'x_grid_T'} )
nav_lon_grid_U = nav_lon_grid_U.rename( {'y':'y_grid_U', 'x':'x_grid_U'} )
nav_lat_grid_U = nav_lat_grid_U.rename( {'y':'y_grid_U', 'x':'x_grid_U'} )
nav_lon_grid_V = nav_lon_grid_V.rename( {'y':'y_grid_V', 'x':'x_grid_V'} )
nav_lat_grid_V = nav_lat_grid_V.rename( {'y':'y_grid_V', 'x':'x_grid_V'} )
nav_lon_grid_W = nav_lon_grid_W.rename( {'y':'y_grid_W', 'x':'x_grid_W'} )
nav_lat_grid_W = nav_lat_grid_W.rename( {'y':'y_grid_W', 'x':'x_grid_W'} )
nav_lon_grid_F = nav_lon_grid_F.rename( {'y':'y_grid_F', 'x':'x_grid_F'} )
nav_lat_grid_F = nav_lat_grid_F.rename( {'y':'y_grid_F', 'x':'x_grid_F'} )

for cd_type in ['T', 'U', 'V', 'F', 'W'] :
    for dir_type in ['lat', 'lon'] :
        coord_name = 'nav_' + dir_type + '_grid_' + cd_type
        locals()[coord_name].encoding['_FillValue'] = None
        locals()[coord_name].encoding['missing_value'] = None

In [18]:
nav_lon_grid_T.name = 'nav_lon_grid_T'
nav_lat_grid_T.name = 'nav_lat_grid_T'
nav_lon_grid_U.name = 'nav_lon_grid_U'
nav_lat_grid_U.name = 'nav_lat_grid_U'
nav_lon_grid_V.name = 'nav_lon_grid_V'
nav_lat_grid_V.name = 'nav_lat_grid_V'
nav_lon_grid_F.name = 'nav_lon_grid_F'
nav_lat_grid_F.name = 'nav_lat_grid_F'
nav_lon_grid_W.name = 'nav_lon_grid_W'
nav_lat_grid_W.name = 'nav_lat_grid_W'

### Add attributes

In [27]:
nav_lon_grid_T.attrs['standard_name'] = 'longitude'
nav_lon_grid_T.attrs['long_name']     = 'Longitude'
nav_lon_grid_T.attrs['units']         = 'degrees_east'
nav_lat_grid_T.attrs['standard_name'] = 'latitude'
nav_lat_grid_T.attrs['long_name']     = 'Latitude'
nav_lat_grid_T.attrs['units']         = 'degrees_north'

nav_lon_grid_U.attrs['standard_name'] = 'longitude'
nav_lon_grid_U.attrs['long_name']     = 'Longitude'
nav_lon_grid_U.attrs['units']         = 'degrees_east'
nav_lat_grid_U.attrs['standard_name'] = 'latitude'
nav_lat_grid_U.attrs['long_name']     = 'Latitude'
nav_lat_grid_U.attrs['units']         = 'degrees_north'

nav_lon_grid_V.attrs['standard_name'] = 'longitude'
nav_lon_grid_V.attrs['long_name']     = 'Longitude'
nav_lon_grid_V.attrs['units']         = 'degrees_east'
nav_lat_grid_V.attrs['standard_name'] = 'latitude'
nav_lat_grid_V.attrs['long_name']     = 'Latitude'
nav_lat_grid_V.attrs['units']         = 'degrees_north'

nav_lon_grid_W.attrs['standard_name'] = 'longitude'
nav_lon_grid_W.attrs['long_name']     = 'Longitude'
nav_lon_grid_W.attrs['units']         = 'degrees_east'
nav_lat_grid_W.attrs['standard_name'] = 'latitude'
nav_lat_grid_W.attrs['long_name']     = 'Latitude'
nav_lat_grid_W.attrs['units']         = 'degrees_north'

nav_lon_grid_F.attrs['standard_name'] = 'longitude'
nav_lon_grid_F.attrs['long_name']     = 'Longitude'
nav_lon_grid_F.attrs['units']         = 'degrees_east'
nav_lat_grid_F.attrs['standard_name'] = 'latitude'
nav_lat_grid_F.attrs['long_name']     = 'Latitude'
nav_lat_grid_F.attrs['units']         = 'degrees_north'

nav_lon_grid_T.attrs['bounds'] = 'bounds_lon_grid_T'
nav_lat_grid_T.attrs['bounds'] = 'bounds_lat_grid_T'
nav_lon_grid_U.attrs['bounds'] = 'bounds_lon_grid_U'
nav_lat_grid_U.attrs['bounds'] = 'bounds_lat_grid_U'
nav_lon_grid_V.attrs['bounds'] = 'bounds_lon_grid_V'
nav_lat_grid_V.attrs['bounds'] = 'bounds_lat_grid_V'
nav_lon_grid_W.attrs['bounds'] = 'bounds_lon_grid_W'
nav_lat_grid_W.attrs['bounds'] = 'bounds_lat_grid_W'
nav_lon_grid_F.attrs['bounds'] = 'bounds_lon_grid_F'
nav_lat_grid_F.attrs['bounds'] = 'bounds_lat_grid_F'

In [20]:
# remove zero values from areas
# need to be define for the extended grid south of -80S
# some point are undefined but you need to have e1 and e2 .NE. 0
for cd_type in ['t', 'u', 'v', 'f'] :
    for axis in ['1', '2'] :
        coordName = 'e' + axis + cd_type
        f_coord[coordName]=xr.where(f_coord[coordName] == 0.0, 1.0e2, f_coord[coordName])

In [21]:
# Correct areas for straits
if model == 'ORCA2.3' :
    # orca_r2: Gibraltar    : e2u reduced to 20 km
    f_coord['e2u'][101,138:140] = 20.e3
    # orca_r2: Bab el Mandeb: e2u reduced to 30 km
    #                         e1v reduced to 18 km
    f_coord['e1v'][87,159] = 18.e3
    f_coord['e2u'][87,159] = 30.e3
    # orca_r2: Danish Straits : e2u reduced to 10 km
    f_coord['e2u'][115,144:146] = 10.e3
    

In [22]:
area_grid_T = nemo.lbc (f_coord ['e1t']*f_coord ['e2t'], nperio=nperio, cd_type='T')
area_grid_U = nemo.lbc (f_coord ['e1u']*f_coord ['e2u'], nperio=nperio, cd_type='U',nemo_4U_bug=True)
#area_grid_U = f_coord ['e1u']*f_coord ['e2u']
area_grid_V = nemo.lbc (f_coord ['e1v']*f_coord ['e2v'], nperio=nperio, cd_type='V')
area_grid_W = nemo.lbc (f_coord ['e1t']*f_coord ['e2t'], nperio=nperio, cd_type='W')
area_grid_F = nemo.lbc (f_coord ['e1f']*f_coord ['e2f'], nperio=nperio, cd_type='F')

area_grid_T.name = 'area_grid_T'
area_grid_U.name = 'area_grid_U'
area_grid_V.name = 'area_grid_V'
area_grid_F.name = 'area_grid_F'
area_grid_W.name = 'area_grid_W'

area_grid_T = area_grid_T.rename ({'y':'y_grid_T', 'x':'x_grid_T'})
area_grid_U = area_grid_U.rename ({'y':'y_grid_U', 'x':'x_grid_U'})
area_grid_V = area_grid_V.rename ({'y':'y_grid_V', 'x':'x_grid_V'})
area_grid_W = area_grid_W.rename ({'y':'y_grid_W', 'x':'x_grid_W'})
area_grid_F = area_grid_F.rename ({'y':'y_grid_F', 'x':'x_grid_F'})

area_grid_T.attrs['standard_name'] = 'cell_area'
area_grid_T.attrs['units']         = 'm2'
area_grid_T.attrs['coordinates']   = 'nav_lat_grid_T nav_lon_grid_T'
area_grid_U.attrs['standard_name'] = 'cell_area'
area_grid_U.attrs['units']         = 'm2'
area_grid_U.attrs['coordinates']   = 'nav_lat_grid_U nav_lon_grid_U'
area_grid_V.attrs['standard_name'] = 'cell_area'
area_grid_V.attrs['units']         = 'm2'
area_grid_V.attrs['coordinates']   = 'nav_lat_grid_V nav_lon_grid_V'
area_grid_W.attrs['standard_name'] = 'cell_area'
area_grid_W.attrs['units']         = 'm2'
area_grid_W.attrs['coordinates']   = 'nav_lat_grid_W nav_lon_grid_W'
area_grid_F.attrs['standard_name'] = 'cell_area'
area_grid_F.attrs['units']         = 'm2'
area_grid_F.attrs['coordinates']   = 'nav_lat_grid_F nav_lon_grid_F'

## Construct bounds

In [23]:
def set_bounds (cdgrd) :
    '''
    Constructs lon/lat bounds
    Bounds are numerated counter clockwise, from bottom left
    See NEMO file OPA_SRC/IOM/iom.F90, ROUTINE set_grid_bounds, for more details
    '''
    # Define offset of coordinate representing bottom-left corner
    if cdgrd in ['T', 'W'] : 
        icnr = -1 ; jcnr = -1
        corner_lon = nav_lon_grid_F ; corner_lat = nav_lat_grid_F
    if cdgrd == 'U'        : 
        icnr =  0 ; jcnr = -1
        corner_lon = nav_lon_grid_V ; corner_lat = nav_lat_grid_V
    if cdgrd == 'V'        : 
        icnr = -1 ; jcnr =  0
        corner_lon = nav_lon_grid_U ; corner_lat = nav_lat_grid_U
    if cdgrd == 'F'        : 
        icnr = -1 ; jcnr = -1
        corner_lon = nav_lon_grid_T ; corner_lat = nav_lat_grid_T

    y_grid, x_grid = corner_lon.shape ; nvertex = 4
    dims = ['y_grid_' + cdgrd, 'x_grid_' + cdgrd, 'nvertex_grid_' + cdgrd]
    
    bounds_lon = xr.DataArray (np.zeros ((y_grid, x_grid, nvertex)), dims=dims)
    bounds_lat = xr.DataArray (np.zeros ((y_grid, x_grid, nvertex)), dims=dims)
    
    idx = [(jcnr,icnr), (jcnr,icnr+1), (jcnr+1,icnr+1), (jcnr+1,icnr)]
    
    # Compute cell vertices that can be defined, 
    # and complete with periodicity
    for nn in range (nvertex) :
        bounds_lon[:,:,nn] = np.roll  (corner_lon, shift=(idx[nn]), axis=(-2,-1))
        bounds_lat[:,:,nn] = np.roll  (corner_lat, shift=(idx[nn]), axis=(-2,-1))
        bounds_lon[:,:,nn] = nemo.lbc (bounds_lon[:,:,nn], nperio=nperio, cd_type=cdgrd)
        bounds_lat[:,:,nn] = nemo.lbc (bounds_lat[:,:,nn], nperio=nperio, cd_type=cdgrd)
    
    # Rotate cells at the north fold
    if nperio >= 3 :
        # Working array for location of northfold
        z_fld = nemo.lbc (np.ones ((jpj, jpi)), nperio=nperio, cd_type=cdgrd, psgn=-1. )
        z_fld = (z_fld == -1.0)
        
        for nn in range (nvertex) :
            nr = np.mod (nn+2, 4)
            bounds_lon[:,:,nn] = np.where (z_fld, bounds_lon[:,:,nr], bounds_lon[:,:,nn])
            bounds_lat[:,:,nn] = np.where (z_fld, bounds_lat[:,:,nr], bounds_lat[:,:,nn])
    
    # Invert cells at the symmetric equator
    if nperio == 2 :
        for nn in range (nvertex) :
            nr = np.mod (nn+2, 4)
            bounds_lon [0, :, nn] = bounds_lon [0, :, nr]
            bounds_lat [0, :, nn] = bounds_lat [0, :, nr]
    
    bounds_lon.attrs['coordinates'] = 'nav_lat_grid_' + cdgrd + ' nav_lon_grid_' + cdgrd
    bounds_lat.attrs['coordinates'] = 'nav_lat_grid_' + cdgrd + ' nav_lon_grid_' + cdgrd
    bounds_lon.attrs['units']       = 'degrees_east'
    bounds_lat.attrs['units']       = 'degrees_north'
    bounds_lon.name = 'bounds_lon_grid_' + cdgrd
    bounds_lat.name = 'bounds_lat_grid_' + cdgrd

    return bounds_lon, bounds_lat

In [24]:
bounds_lon_grid_T, bounds_lat_grid_T = set_bounds ('T')
bounds_lon_grid_U, bounds_lat_grid_U = set_bounds ('U')
bounds_lon_grid_V, bounds_lat_grid_V = set_bounds ('V')
bounds_lon_grid_W, bounds_lat_grid_W = set_bounds ('W')
bounds_lon_grid_F, bounds_lat_grid_F = set_bounds ('F')

## Save Data in a NetCDF file

In [28]:
ds = xr.Dataset ({
    'mask_T'      : mask_T     ,
    'mask_U'      : mask_U     ,
    'mask_V'      : mask_V     ,
    'mask_W'      : mask_W     ,
    'mask_F'      : mask_F     ,
    'area_grid_T' : area_grid_T,
    'area_grid_U' : area_grid_U,
    'area_grid_V' : area_grid_V,
    'area_grid_W' : area_grid_W,
    'area_grid_F' : area_grid_F,
    'maskutil_T'  : maskutil_T ,
    'maskutil_U'  : maskutil_U ,
    'maskutil_V'  : maskutil_V ,
    'maskutil_W'  : maskutil_W ,
    'maskutil_F'  : maskutil_F ,
    'bounds_lon_grid_T': bounds_lon_grid_T,
    'bounds_lat_grid_T': bounds_lat_grid_T,
    'bounds_lon_grid_U': bounds_lon_grid_U,
    'bounds_lat_grid_U': bounds_lat_grid_U,
    'bounds_lon_grid_V': bounds_lon_grid_V,
    'bounds_lat_grid_V': bounds_lat_grid_V,
    'bounds_lon_grid_W': bounds_lon_grid_W,
    'bounds_lat_grid_W': bounds_lat_grid_W,
    'bounds_lon_grid_F': bounds_lon_grid_F,
    'bounds_lat_grid_F': bounds_lat_grid_F,
})
for cd_type in ['T', 'U', 'V', 'F', 'W'] :
    for dir_type in ['lat', 'lon'] :
        coord_name = 'nav_' + dir_type + '_grid_' + cd_type
        ds.coords[coord_name]=locals()[coord_name]

ds.attrs['name']         = 'coordinates_mask'
ds.attrs['description']  = 'coordinates and mask for MOSAIX'
ds.attrs['title']        = 'coordinates_mask'
ds.attrs['source']       = 'IPSL Earth system model'
ds.attrs['group']        = 'ICMC IPSL Climate Modelling Center'
ds.attrs['Institution']  = 'IPSL https.//www.ipsl.fr'
ds.attrs['Model']        = model
ds.attrs['timeStamp']    = '{:%Y-%b-%d %H:%M:%S}'.format (datetime.datetime.now ())
ds.attrs['history']      = 'Build from ' + n_coord + ' and ' + n_bathy
ds.attrs['directory']    = os.getcwd     ()
ds.attrs['user']         = os.getlogin   ()
ds.attrs['HOSTNAME']     = platform.node ()
ds.attrs['Python']       = 'Python version: ' +  platform.python_version ()
ds.attrs['xarray']       = 'xarray version: ' +  xr.__version__
ds.attrs['OS']           = platform.system  ()
ds.attrs['release']      = platform.release ()
ds.attrs['hardware']     = platform.machine ()

ds.attrs['SVN_Author']   = "$Author:  $"
ds.attrs['SVN_Date']     = "$Date:  $"
ds.attrs['SVN_Revision'] = "$Revision:  $"
ds.attrs['SVN_Id']       = "$Id: Build_coordinates_mask.py $"
ds.attrs['SVN_HeadURL']  = "$HeadURL: http://forge.ipsl.jussieu.fr/igcmg/svn/TOOLS/MOSAIX/Build_coordinates_mask.py $"

In [ ]:
# Why is this necessary ?
ds['nav_lon_grid_T'].attrs['bounds'] = nav_lon_grid_T.attrs['bounds']
ds['nav_lat_grid_T'].attrs['bounds'] = nav_lat_grid_T.attrs['bounds']
ds['nav_lon_grid_U'].attrs['bounds'] = nav_lon_grid_U.attrs['bounds']
ds['nav_lat_grid_U'].attrs['bounds'] = nav_lat_grid_U.attrs['bounds']
ds['nav_lon_grid_V'].attrs['bounds'] = nav_lon_grid_V.attrs['bounds']
ds['nav_lat_grid_V'].attrs['bounds'] = nav_lat_grid_V.attrs['bounds']
ds['nav_lon_grid_W'].attrs['bounds'] = nav_lon_grid_W.attrs['bounds']
ds['nav_lat_grid_W'].attrs['bounds'] = nav_lat_grid_W.attrs['bounds']
ds['nav_lon_grid_F'].attrs['bounds'] = nav_lon_grid_F.attrs['bounds']
ds['nav_lat_grid_F'].attrs['bounds'] = nav_lat_grid_F.attrs['bounds']

In [29]:
ds.to_netcdf (n_out)

# That's all folk's !